In [ ]:
# Creating a virtual environment
!python3 -m venv deeprl
!source deeprl/bin/activate

In [1]:
# Installing Required Libraries
%pip install stable-baselines3[extra]
%pip install gymnasium
%pip install huggingface_sb3
%pip install huggingface_hub
%pip install panda_gym


zsh:1: no matches found: stable-baselines3[extra]
Note: you may need to restart the kernel to use updated packages.
  Using cached gymnasium-0.29.1-py3-none-any.whl (953 kB)
  Using cached Farama_Notifications-0.0.4-py3-none-any.whl (2.5 kB)
  Using cached cloudpickle-3.0.0-py3-none-any.whl (20 kB)
  Using cached numpy-1.26.3-cp39-cp39-macosx_11_0_arm64.whl (14.0 MB)
You should consider upgrading via the '/Users/amankankriya/Documents/Deep RL/deeprl/bin/python -m pip install --upgrade pip' command.
Note: you may need to restart the kernel to use updated packages.
  Using cached huggingface_sb3-3.0-py3-none-any.whl (9.7 kB)
  Using cached PyYAML-6.0.1-cp39-cp39-macosx_11_0_arm64.whl (174 kB)
  Using cached wasabi-1.1.2-py3-none-any.whl (27 kB)
  Using cached huggingface_hub-0.20.3-py3-none-any.whl (330 kB)
  Using cached fsspec-2023.12.2-py3-none-any.whl (168 kB)
  Using cached requests-2.31.0-py3-none-any.whl (62 kB)
  Using cached filelock-3.13.1-py3-none-any.whl (11 kB)
  Using cache

In [2]:
# Importing the packages
import os

import gymnasium as gym
import panda_gym

from huggingface_sb3 import load_from_hub, package_to_hub

from stable_baselines3 import A2C
from stable_baselines3.common.evaluation import evaluate_policy
from stable_baselines3.common.vec_env import DummyVecEnv, VecNormalize
from stable_baselines3.common.env_util import make_vec_env

from huggingface_hub import notebook_login

/Users/amankankriya/Documents/Deep RL/deeprl/lib/python3.9/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [4]:
import torch
torch.device('mps')

device(type='mps')

In [5]:
env_id = "PandaReachDense-v3"

# Create the env
env = gym.make(env_id)

# Get the state space and action space
s_size = env.observation_space.shape
a_size = env.action_space

pybullet build time: Jan 28 2024 10:11:19


argv[0]=--background_color_red=0.8745098114013672
argv[1]=--background_color_green=0.21176470816135406
argv[2]=--background_color_blue=0.1764705926179886


In [6]:
env = make_vec_env(env_id, n_envs=4)
env = VecNormalize(env, norm_obs=True, norm_reward=True, clip_obs=10.)

argv[0]=--background_color_red=0.8745098114013672
argv[1]=--background_color_green=0.21176470816135406
argv[2]=--background_color_blue=0.1764705926179886
argv[0]=--background_color_red=0.8745098114013672
argv[1]=--background_color_green=0.21176470816135406
argv[2]=--background_color_blue=0.1764705926179886
argv[0]=--background_color_red=0.8745098114013672
argv[1]=--background_color_green=0.21176470816135406
argv[2]=--background_color_blue=0.1764705926179886
argv[0]=--background_color_red=0.8745098114013672
argv[1]=--background_color_green=0.21176470816135406
argv[2]=--background_color_blue=0.1764705926179886


In [12]:
model = A2C(policy = "MultiInputPolicy",
            env = env,
            verbose=1,
            device='mps')

Using mps device


In [13]:
model.learn(10_000_000)

------------------------------------
| rollout/              |          |
|    ep_len_mean        | 41.7     |
|    ep_rew_mean        | -14.5    |
| time/                 |          |
|    fps                | 213      |
|    iterations         | 100      |
|    time_elapsed       | 9        |
|    total_timesteps    | 2000     |
| train/                |          |
|    entropy_loss       | -4.27    |
|    explained_variance | 0.885    |
|    learning_rate      | 0.0007   |
|    n_updates          | 99       |
|    policy_loss        | -1.2     |
|    std                | 1.01     |
|    value_loss         | 0.109    |
------------------------------------
------------------------------------
| rollout/              |          |
|    ep_len_mean        | 44.2     |
|    ep_rew_mean        | -15.4    |
| time/                 |          |
|    fps                | 279      |
|    iterations         | 200      |
|    time_elapsed       | 14       |
|    total_timesteps    | 4000     |
|

In [14]:
model.save("a2c-PandaReachDense-v3")
env.save("vec_normalize.pkl")

In [15]:
from stable_baselines3.common.vec_env import DummyVecEnv, VecNormalize

# Load the saved statistics
eval_env = DummyVecEnv([lambda: gym.make("PandaReachDense-v3")])
eval_env = VecNormalize.load("vec_normalize.pkl", eval_env)

# We need to override the render_mode
eval_env.render_mode = "rgb_array"

#  do not update them at test time
eval_env.training = False
# reward normalization is not needed at test time
eval_env.norm_reward = False

# Load the agent
model = A2C.load("a2c-PandaReachDense-v3")

mean_reward, std_reward = evaluate_policy(model, eval_env)

print(f"Mean reward = {mean_reward:.2f} +/- {std_reward:.2f}")

argv[0]=--background_color_red=0.8745098114013672
argv[1]=--background_color_green=0.21176470816135406
argv[2]=--background_color_blue=0.1764705926179886
Mean reward = -0.20 +/- 0.12


/Users/amankankriya/Documents/Deep RL/deeprl/lib/python3.9/site-packages/stable_baselines3/common/evaluation.py:67: UserWarning: Evaluation environment is not wrapped with a ``Monitor`` wrapper. This may result in reporting modified episode lengths and rewards, if other wrappers happen to modify these. Consider wrapping environment first with ``Monitor`` wrapper.
  warnings.warn(


In [28]:
from huggingface_sb3 import package_to_hub

package_to_hub(
    model=model,
    model_name=f"a2c-{env_id}",
    model_architecture="A2C",
    env_id=env_id,
    eval_env=eval_env,
    repo_id=f"Amankankriya/a22c-{env_id}", # Change the username
    commit_message="Initial commit",
)

ℹ This function will save, evaluate, generate a video of your agent,
create a model card and push everything to the hub. It might take up to 1min.
This is a work in progress: if you encounter a bug, please open an issue.


Exception ignored in: <function VecVideoRecorder.__del__ at 0x179df5700>
Traceback (most recent call last):
  File "/Users/amankankriya/Documents/Deep RL/deeprl/lib/python3.9/site-packages/stable_baselines3/common/vec_env/vec_video_recorder.py", line 113, in __del__
    self.close_video_recorder()
  File "/Users/amankankriya/Documents/Deep RL/deeprl/lib/python3.9/site-packages/stable_baselines3/common/vec_env/vec_video_recorder.py", line 104, in close_video_recorder
    self.video_recorder.close()
  File "/Users/amankankriya/Documents/Deep RL/deeprl/lib/python3.9/site-packages/gymnasium/wrappers/monitoring/video_recorder.py", line 149, in close
    from moviepy.video.io.ImageSequenceClip import ImageSequenceClip
  File "/Users/amankankriya/Documents/Deep RL/deeprl/lib/python3.9/site-packages/moviepy/video/io/ImageSequenceClip.py", line 6, in <module>
    from ..VideoClip import VideoClip
  File "/Users/amankankriya/Documents/Deep RL/deeprl/lib/python3.9/site-packages/moviepy/video/Vide

Saving video to /var/folders/54/9xphnqpn00b76nztg29d2t8w0000gn/T/tmpzjmlf8y6/-step-0-to-step-1000.mp4
✘ No ffmpeg exe could be found. Install ffmpeg on your system, or set
the IMAGEIO_FFMPEG_EXE environment variable.
✘ We are unable to generate a replay of your agent, the package_to_hub
process continues
✘ Please open an issue at
https://github.com/huggingface/huggingface_sb3/issues
ℹ Pushing repo Amankankriya/a22c-PandaReachDense-v3 to the Hugging Face
Hub





policy.pth:   0%|          | 0.00/46.3k [00:00<?, ?B/s]









policy.pth:  35%|███▌      | 16.4k/46.3k [00:01<00:02, 14.4kB/s]


policy.optimizer.pth: 100%|██████████| 45.0k/45.0k [00:01<00:00, 26.1kB/s]
pytorch_variables.pth: 100%|██████████| 864/864 [00:02<00:00, 418B/s]
vec_normalize.pkl: 100%|██████████| 2.66k/2.66k [00:02<00:00, 1.26kB/s]
policy.pth: 100%|██████████| 46.3k/46.3k [00:02<00:00, 20.2kB/s]
a2c-PandaReachDense-v3.zip: 100%|██████████| 110k/110k [00:02<00:00, 45.4kB/s] 








Upload 5 LFS files: 100%|██████████| 5/5 [00:03<00:00,  1.56it/s]


ℹ Your model is pushed to the Hub. You can view your model here:
https://huggingface.co/Amankankriya/a22c-PandaReachDense-v3/tree/main/


CommitInfo(commit_url='https://huggingface.co/Amankankriya/a22c-PandaReachDense-v3/commit/0875cd19a50cc091d8112ffc30000ccd4b6aeef3', commit_message='Initial commit', commit_description='', oid='0875cd19a50cc091d8112ffc30000ccd4b6aeef3', pr_url=None, pr_revision=None, pr_num=None)